🚌 Projet MDM - Mobilité Durable en Montagne ⛰️

*Author : Nicolas Grosjean*

*Date : 13/09/2025*

**Description :**

This Jupyter Notebook analyses the OSM data

In [12]:
import folium
import geopandas as gpd
import pandas as pd

In [2]:
import os

os.chdir("../..")
print("Working directory set to the root of the project")

Working directory set to the root of the project


In [3]:
from src.processors.osm import OSMBusLinesProcessor, OSMBusStopsProcessor

In [4]:
def get_markdown_dtype(df: pd.DataFrame):
    markdown_table = "| Column | Dtype |\n|--------|-------|\n"
    for col in df.columns:
        non_null = df[col].count()
        dtype = df[col].dtype
        markdown_table += f"| {col} | {dtype} |\n"
    return markdown_table

In [5]:
stops_gdf = OSMBusStopsProcessor.fetch(reload_pipeline=False)
stops_gdf.head()

gtfs_id navitia_id  osm_id                    name  \
0    None       None  135296  Université - IUT-STAPS   
1    None       None  135930   Hôpital Couple Enfant   
2    None       None  136570              Cap des H'   
3    None       None  136597  Place de la Libération   
4    None       None  137073             Centr'Alp 2   

                            description line_gtfs_ids  \
0                                  None            []   
1                                  None            []   
2  Arrêt de régulation, non commercial.            []   
3                                  None            []   
4                                  None            []   

                                        line_osm_ids network network_gtfs_id  \
0                                          [3922428]  M réso            None   
1                                 [3333927, 3922430]  M réso            None   
2                                                 []  M réso            None   
3  [3031947, 3031948, 3044780, 3044781, 3923550, ...  M réso            None   
4                                 [8671286, 8671287]  M réso            None   

                   geometry                                              other  
0  POINT (5.77622 45.19738)  {'alt_name': None, 'amenity': None, 'bench': N...  
1  POINT (5.74231 45.20065)  {'alt_name': None, 'amenity': None, 'bench': N...  
2  POINT (5.68159 45.21695)  {'alt_name': None, 'amenity': None, 'bench': N...  
3  POINT (5.66272 45.20707)  {'alt_name': None, 'amenity': None, 'bench': N...  
4    POINT (5.6043 45.3198)  {'alt_name': None, 'amenity': None, 'bench': N...

In [6]:
stops_gdf.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 6806 entries, 0 to 6805
Data columns (total 11 columns):
 #   Column           Non-Null Count  Dtype   
---  ------           --------------  -----   
 0   gtfs_id          595 non-null    object  
 1   navitia_id       0 non-null      object  
 2   osm_id           6806 non-null   int64   
 3   name             6806 non-null   object  
 4   description      276 non-null    object  
 5   line_gtfs_ids    6806 non-null   object  
 6   line_osm_ids     6806 non-null   object  
 7   network          4816 non-null   object  
 8   network_gtfs_id  0 non-null      object  
 9   geometry         6806 non-null   geometry
 10  other            6806 non-null   object  
dtypes: geometry(1), int64(1), object(9)
memory usage: 585.0+ KB


In [7]:
expanded = stops_gdf["other"].apply(pd.Series)
expanded_stops_gdf = pd.concat([stops_gdf.drop(columns=["other"]), expanded], axis=1)
expanded_stops_gdf[expanded_stops_gdf.columns[:10]].head()

gtfs_id navitia_id  osm_id                    name  \
0    None       None  135296  Université - IUT-STAPS   
1    None       None  135930   Hôpital Couple Enfant   
2    None       None  136570              Cap des H'   
3    None       None  136597  Place de la Libération   
4    None       None  137073             Centr'Alp 2   

                            description line_gtfs_ids  \
0                                  None            []   
1                                  None            []   
2  Arrêt de régulation, non commercial.            []   
3                                  None            []   
4                                  None            []   

                                        line_osm_ids network network_gtfs_id  \
0                                          [3922428]  M réso            None   
1                                 [3333927, 3922430]  M réso            None   
2                                                 []  M réso            None   
3  [3031947, 3031948, 3044780, 3044781, 3923550, ...  M réso            None   
4                                 [8671286, 8671287]  M réso            None   

                   geometry  
0  POINT (5.77622 45.19738)  
1  POINT (5.74231 45.20065)  
2  POINT (5.68159 45.21695)  
3  POINT (5.66272 45.20707)  
4    POINT (5.6043 45.3198)

In [8]:
expanded_stops_gdf.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 6806 entries, 0 to 6805
Data columns (total 79 columns):
 #   Column                         Non-Null Count  Dtype   
---  ------                         --------------  -----   
 0   gtfs_id                        595 non-null    object  
 1   navitia_id                     0 non-null      object  
 2   osm_id                         6806 non-null   int64   
 3   name                           6806 non-null   object  
 4   description                    276 non-null    object  
 5   line_gtfs_ids                  6806 non-null   object  
 6   line_osm_ids                   6806 non-null   object  
 7   network                        4816 non-null   object  
 8   network_gtfs_id                0 non-null      object  
 9   geometry                       6806 non-null   geometry
 10  alt_name                       32 non-null     object  
 11  amenity                        3 non-null      object  
 12  bench                     

In [9]:
print(
    get_markdown_dtype(expanded_stops_gdf[expanded_stops_gdf.columns[:10]]).replace(
        "object", "string"
    )
)

| Column | Dtype |
|--------|-------|
| gtfs_id | string |
| navitia_id | string |
| osm_id | int64 |
| name | string |
| description | string |
| line_gtfs_ids | string |
| line_osm_ids | string |
| network | string |
| network_gtfs_id | string |
| geometry | geometry |



In [10]:
lines_df = OSMBusLinesProcessor.fetch(reload_pipeline=False)
lines_df.head()

gtfs_id   osm_id                                               name  \
0    None  2067887  Ligne A : Gare de Saint-Clair-Les-Roches ⇒ Ron...   
1    None  2569190  Ouibus 70 : Grenoble Gare Routière -> Aéroport...   
2    None  2569239  Ouibus 70 : Aéroport Lyon Saint-Exupéry -> Pla...   
3    None  2920548   15 : Bois Français => Grenoble (via Chenevières)   
4    None  2920549   15 : Grenoble => Bois Français (via Chenevières)   

                              from_location  \
0            Gare de Saint-Clair-Les-Roches   
1                  Grenoble - Gare Routière   
2  Aéroport Lyon Saint-Exupéry - Terminal 1   
3              Saint Ismier - Bois Français   
4              Grenoble - Verdun-Préfecture   

                                         to    network network_gtfs_id  \
0                         Rond-point Chanas        TPR            None   
1  Aéroport Lyon Saint-Exupéry - Terminal 1  BlaBlaBus            None   
2                  Grenoble - Gare routière  BlaBlaBus            None   
3              Grenoble - Verdun-Préfecture     M réso            None   
4              Saint Ismier - Bois Français     M réso            None   

  network_wikidata                       operator   colour text_colour  \
0             None  Courriers Rhodaniens / Fayard   e53b1a        None   
1         Q1653380                  Faure Vercors  #ee0064        None   
2         Q1653380                  Faure Vercors  #ee0064        None   
3       Q131689044                            VFD  #1f72b9        None   
4       Q131689044                            VFD  #1f72b9        None   

  stop_gtfs_ids                                      stops_osm_ids  school  \
0            []  [1659415935, 8874916309, 11146173165, 11146173...   False   
1            []                [2617010911, 474827289, 6074566590]   False   
2            []                [6074566590, 457759141, 2617010911]   False   
3            []  [2299463674, 513946287, 513946283, 513946279, ...   False   
4            []  [372746162, 451116247, 1829688368, 1829874475,...   False   

  geometry                                              other  
0     None  {'charge': None, 'check_date': None, 'comment'...  
1     None  {'charge': None, 'check_date': None, 'comment'...  
2     None  {'charge': None, 'check_date': None, 'comment'...  
3     None  {'charge': None, 'check_date': None, 'comment'...  
4     None  {'charge': None, 'check_date': None, 'comment'...

In [11]:
lines_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1874 entries, 0 to 1873
Data columns (total 16 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   gtfs_id           335 non-null    object
 1   osm_id            1874 non-null   int64 
 2   name              1874 non-null   object
 3   from_location     1870 non-null   object
 4   to                1870 non-null   object
 5   network           1868 non-null   object
 6   network_gtfs_id   0 non-null      object
 7   network_wikidata  1487 non-null   object
 8   operator          1613 non-null   object
 9   colour            1445 non-null   object
 10  text_colour       34 non-null     object
 11  stop_gtfs_ids     1874 non-null   object
 12  stops_osm_ids     1874 non-null   object
 13  school            1874 non-null   bool  
 14  geometry          0 non-null      object
 15  other             1874 non-null   object
dtypes: bool(1), int64(1), object(14)
memory usage: 221.6+ KB


In [12]:
expanded = lines_df["other"].apply(pd.Series)
expanded_lines_df = pd.concat([lines_df.drop(columns=["other"]), expanded], axis=1)
expanded_lines_df.head()

gtfs_id   osm_id                                               name  \
0    None  2067887  Ligne A : Gare de Saint-Clair-Les-Roches ⇒ Ron...   
1    None  2569190  Ouibus 70 : Grenoble Gare Routière -> Aéroport...   
2    None  2569239  Ouibus 70 : Aéroport Lyon Saint-Exupéry -> Pla...   
3    None  2920548   15 : Bois Français => Grenoble (via Chenevières)   
4    None  2920549   15 : Grenoble => Bois Français (via Chenevières)   

                              from_location  \
0            Gare de Saint-Clair-Les-Roches   
1                  Grenoble - Gare Routière   
2  Aéroport Lyon Saint-Exupéry - Terminal 1   
3              Saint Ismier - Bois Français   
4              Grenoble - Verdun-Préfecture   

                                         to    network network_gtfs_id  \
0                         Rond-point Chanas        TPR            None   
1  Aéroport Lyon Saint-Exupéry - Terminal 1  BlaBlaBus            None   
2                  Grenoble - Gare routière  BlaBlaBus            None   
3              Grenoble - Verdun-Préfecture     M réso            None   
4              Saint Ismier - Bois Français     M réso            None   

  network_wikidata                       operator   colour  ... roundtrip  \
0             None  Courriers Rhodaniens / Fayard   e53b1a  ...      None   
1         Q1653380                  Faure Vercors  #ee0064  ...      None   
2         Q1653380                  Faure Vercors  #ee0064  ...      None   
3       Q131689044                            VFD  #1f72b9  ...      None   
4       Q131689044                            VFD  #1f72b9  ...      None   

  route seasonal  segment source   type   url  \
0   bus     None     None   None  route  None   
1   bus     None     None   None  route  None   
2   bus     None     None   None  route  None   
3   bus     None     None   None  route  None   
4   bus     None     None   None  route  None   

                                  via website wheelchair  
0  Le Péage de Roussillon - Gare SNCF    None       None  
1              Place de la résistance    None       None  
2              Place de la Résistance    None       None  
3                Domène - Chenevières    None        yes  
4                Domène - Chenevières    None        yes  

[5 rows x 72 columns]

In [13]:
expanded_lines_df.loc[4, expanded_lines_df.columns[:25]]

gtfs_id                                                          None
osm_id                                                        2920549
name                 15 : Grenoble => Bois Français (via Chenevières)
from_location                            Grenoble - Verdun-Préfecture
to                                       Saint Ismier - Bois Français
network                                                        M réso
network_gtfs_id                                                  None
network_wikidata                                           Q131689044
operator                                                          VFD
colour                                                        #1f72b9
text_colour                                                      None
stop_gtfs_ids                                                      []
stops_osm_ids       [372746162, 451116247, 1829688368, 1829874475,...
school                                                          False
geometry            

In [14]:
expanded_lines_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1874 entries, 0 to 1873
Data columns (total 72 columns):
 #   Column                    Non-Null Count  Dtype 
---  ------                    --------------  ----- 
 0   gtfs_id                   335 non-null    object
 1   osm_id                    1874 non-null   int64 
 2   name                      1874 non-null   object
 3   from_location             1870 non-null   object
 4   to                        1870 non-null   object
 5   network                   1868 non-null   object
 6   network_gtfs_id           0 non-null      object
 7   network_wikidata          1487 non-null   object
 8   operator                  1613 non-null   object
 9   colour                    1445 non-null   object
 10  text_colour               34 non-null     object
 11  stop_gtfs_ids             1874 non-null   object
 12  stops_osm_ids             1874 non-null   object
 13  school                    1874 non-null   bool  
 14  geometry                

In [15]:
print(
    get_markdown_dtype(expanded_lines_df[expanded_lines_df.columns[:25]]).replace(
        "object", "string"
    )
)

| Column | Dtype |
|--------|-------|
| gtfs_id | string |
| osm_id | int64 |
| name | string |
| from_location | string |
| to | string |
| network | string |
| network_gtfs_id | string |
| network_wikidata | string |
| operator | string |
| colour | string |
| text_colour | string |
| stop_gtfs_ids | string |
| stops_osm_ids | string |
| school | bool |
| geometry | string |
| charge | string |
| check_date | string |
| comment | string |
| description | string |
| description:ca | string |
| description:de | string |
| description:es | string |
| description:fr | string |
| duration | string |
| fee | string |



In [34]:
lines_gdf = OSMBusLinesProcessor.fetch(
    reload_pipeline=False,
    fetch_api_kwargs={"fetch_geometry": True},
    fetch_input_kwargs={"fetch_geometry": True},
    fetch_output_kwargs={"fetch_geometry": True},
)
lines_gdf.head()

gtfs_id   osm_id                                               name  \
0    None  2067887  Ligne A : Gare de Saint-Clair-Les-Roches ⇒ Ron...   
1    None  2569190  Ouibus 70 : Grenoble Gare Routière -> Aéroport...   
2    None  2569239  Ouibus 70 : Aéroport Lyon Saint-Exupéry -> Pla...   
3    None  2920548   15 : Bois Français => Grenoble (via Chenevières)   
4    None  2920549   15 : Grenoble => Bois Français (via Chenevières)   

                              from_location  \
0            Gare de Saint-Clair-Les-Roches   
1                  Grenoble - Gare Routière   
2  Aéroport Lyon Saint-Exupéry - Terminal 1   
3              Saint Ismier - Bois Français   
4              Grenoble - Verdun-Préfecture   

                                         to    network network_gtfs_id  \
0                         Rond-point Chanas        TPR            None   
1  Aéroport Lyon Saint-Exupéry - Terminal 1  BlaBlaBus            None   
2                  Grenoble - Gare routière  BlaBlaBus            None   
3              Grenoble - Verdun-Préfecture     M réso            None   
4              Saint Ismier - Bois Français     M réso            None   

  network_wikidata                       operator   colour text_colour  \
0             None  Courriers Rhodaniens / Fayard   e53b1a        None   
1         Q1653380                  Faure Vercors  #ee0064        None   
2         Q1653380                  Faure Vercors  #ee0064        None   
3       Q131689044                            VFD  #1f72b9        None   
4       Q131689044                            VFD  #1f72b9        None   

  stop_gtfs_ids                                      stops_osm_ids  school  \
0            []  [1659415935, 8874916309, 11146173165, 11146173...   False   
1            []                [2617010911, 474827289, 6074566590]   False   
2            []                [6074566590, 457759141, 2617010911]   False   
3            []  [2299463674, 513946287, 513946283, 513946279, ...   False   
4            []  [372746162, 451116247, 1829688368, 1829874475,...   False   

                                            geometry  \
0  MULTILINESTRING ((4.76919 45.45084, 4.76921 45...   
1  MULTILINESTRING ((5.71428 45.19292, 5.71419 45...   
2  MULTILINESTRING ((5.07924 45.71927, 5.07917 45...   
3  MULTILINESTRING ((5.83771 45.22482, 5.83755 45...   
4  MULTILINESTRING ((5.73167 45.18833, 5.73175 45...   

                                               other  
0  {'charge': None, 'check_date': None, 'comment'...  
1  {'charge': None, 'check_date': None, 'comment'...  
2  {'charge': None, 'check_date': None, 'comment'...  
3  {'charge': None, 'check_date': None, 'comment'...  
4  {'charge': None, 'check_date': None, 'comment'...

In [35]:
lines_gdf.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 1874 entries, 0 to 1873
Data columns (total 16 columns):
 #   Column            Non-Null Count  Dtype   
---  ------            --------------  -----   
 0   gtfs_id           335 non-null    object  
 1   osm_id            1874 non-null   int64   
 2   name              1874 non-null   object  
 3   from_location     1870 non-null   object  
 4   to                1870 non-null   object  
 5   network           1868 non-null   object  
 6   network_gtfs_id   0 non-null      object  
 7   network_wikidata  1487 non-null   object  
 8   operator          1613 non-null   object  
 9   colour            1445 non-null   object  
 10  text_colour       34 non-null     object  
 11  stop_gtfs_ids     1874 non-null   object  
 12  stops_osm_ids     1874 non-null   object  
 13  school            1874 non-null   bool    
 14  geometry          1874 non-null   geometry
 15  other             1874 non-null   object  
dtypes: bool(1), geom

In [36]:
c4_gdf = lines_gdf[lines_gdf["name"].apply(lambda s: "C4" in s)]
print("Display Bus line C4")
c4_gdf.explore()

Display Bus line C4


In [39]:
# Add a base OSM map centered on Grenoble
m = folium.Map(location=[45.1885, 5.7245], zoom_start=12, tiles="OpenStreetMap")

# Add Waymarked Trails hiking layers
folium.TileLayer(tiles="WaymarkedTrails.hiking").add_to(m)

# Add some bus lines
BUS_LINE_NUMBER = 200
for _, r in lines_gdf.iloc[:BUS_LINE_NUMBER].iterrows():
    sim_geo = gpd.GeoSeries(r["geometry"])
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j, style_function=lambda x: {"color": "green"})
    folium.Popup(r["name"]).add_to(geo_j)
    geo_j.add_to(m)
m